In [1]:
import sys
print(sys.version)

3.7.3 (default, Mar 27 2019, 22:11:17) 
[GCC 7.3.0]


In [1]:
import pandas as pd
import keras
import cv2
import os
import matplotlib.pyplot as plt
from keras.applications.vgg16 import VGG16
import numpy as np
from keras.utils import to_categorical
from keras.layers import Dense, Dropout, Flatten
from sklearn.model_selection import train_test_split

Using TensorFlow backend.


In [14]:
folders = ["0-PALM", "1-THUMBSUP", "2-VICTORY", "3-POINT", "4-ROCK", "5-OK"]

In [15]:
images = pd.DataFrame(columns=["path", "gesture"])
for folder in folders:
    for f_name in os.listdir('inputs/'+folder):
        images = images.append({"path": 'inputs/'+folder+'/'+f_name, "gesture": folder[0]}, ignore_index=True)

        
display(images.head())

path gesture
0    inputs/0-PALM/B_P_hgr1_id08_1.jpg       0
1    inputs/0-PALM/B_P_hgr1_id12_2.jpg       0
2  inputs/0-PALM/5_A_hgr2A2_id02_1.bmp       0
3    inputs/0-PALM/B_P_hgr1_id12_2.bmp       0
4    inputs/0-PALM/B_P_hgr1_id06_2.jpg       0

In [4]:
img = cv2.imread(images["path"][0], cv2.IMREAD_COLOR)

In [5]:
img_resized = cv2.resize(img, (50,50), interpolation = cv2.INTER_AREA)

In [6]:
imgYCC = cv2.cvtColor(img_resized, cv2.COLOR_BGR2YCR_CB)

In [7]:
print(imgYCC.shape)
height, width = imgYCC.shape[:2]

middle_color = imgYCC[25,25]
y_range = 20
cb_range = 15
cr_range = 10

(50, 50, 3)


In [3]:
def processImage(img):
    img_resized = cv2.resize(img, (100,100), interpolation = cv2.INTER_AREA)
    imgYCC = cv2.cvtColor(img_resized, cv2.COLOR_BGR2YCR_CB)
    height, width = imgYCC.shape[:2]
    middle_color = imgYCC[25,25]
    y_range = 20
    cb_range = 15
    cr_range = 10
    return imgYCC

def addRotations(img):
    for angle in range(0, 360, 15):
        rotated = imutils.rotate(img, angle)
        cv2.imshow("Rotated (Problematic)", rotated)
        cv2.waitKey(0)
    
img = cv2.imread(images["path"][0], cv2.IMREAD_COLOR)
processImage(images["path"][0])


NameError: name 'images' is not defined

In [10]:
'''M = cv2.getRotationMatrix2D((len(img/2),len(img/2)), 45, 1)
rotated180 = cv2.warpAffine(img, M, (len(img/2),len(img/2))) 

cv2.imshow('Original Image',rotated180)
cv2.waitKey(0) # waits until a key is pressed
cv2.destroyAllWindows() # destroys the window showing image'''

"M = cv2.getRotationMatrix2D((len(img/2),len(img/2)), 45, 1)\nrotated180 = cv2.warpAffine(img, M, (len(img/2),len(img/2))) \n\ncv2.imshow('Original Image',rotated180)\ncv2.waitKey(0) # waits until a key is pressed\ncv2.destroyAllWindows() # destroys the window showing image"

In [16]:
from imutils import rotate_bound


In [17]:
X = []
y = []
for i in range(len(images)):
    img = cv2.imread(images["path"][i], cv2.IMREAD_COLOR)
    for angle in np.arange(0, 360, 45):
        rotated = rotate_bound(img, angle)
        X.append(processImage(rotated))
        y.append(images["gesture"][i])

In [19]:
print(X)

[array([[[ 30, 117, 140],
        [ 31, 117, 141],
        [ 33, 116, 141],
        ...,
        [ 22, 119, 139],
        [ 21, 119, 139],
        [ 21, 119, 138]],

       [[ 31, 116, 141],
        [ 33, 116, 141],
        [ 33, 116, 142],
        ...,
        [ 23, 118, 139],
        [ 22, 119, 139],
        [ 21, 119, 138]],

       [[ 32, 116, 142],
        [ 33, 116, 142],
        [ 33, 117, 142],
        ...,
        [ 24, 118, 139],
        [ 23, 118, 139],
        [ 22, 119, 138]],

       ...,

       [[ 29, 117, 140],
        [ 29, 117, 140],
        [ 29, 117, 140],
        ...,
        [ 21, 119, 138],
        [ 19, 119, 139],
        [ 15, 122, 135]],

       [[ 29, 117, 140],
        [ 29, 117, 140],
        [ 29, 117, 140],
        ...,
        [ 19, 120, 136],
        [ 16, 122, 135],
        [  7, 127, 131]],

       [[ 28, 117, 139],
        [ 29, 117, 139],
        [ 29, 117, 140],
        ...,
        [  7, 127, 130],
        [  7, 127, 129],
        [  6, 128, 129]

In [14]:
'''X_train = X[:183]
X_test = X[183:]
y_train = y[:183]
y_test = y[183:]'''

'X_train = X[:183]\nX_test = X[183:]\ny_train = y[:183]\ny_test = y[183:]'

In [18]:
tr_files, aux_files, tr_labels, aux_labels = \
    train_test_split(X, y, test_size=0.3, random_state=42, stratify=y)

te_files, va_files, te_labels, va_labels = \
    train_test_split(aux_files, aux_labels, test_size=0.5, random_state=42, stratify=aux_labels)

print(tr_files)

[array([[[ 54, 127, 130],
        [ 57, 127, 130],
        [ 57, 127, 130],
        ...,
        [ 67, 127, 130],
        [ 66, 127, 130],
        [ 63, 127, 130]],

       [[ 75, 126, 130],
        [ 78, 127, 130],
        [ 83, 126, 130],
        ...,
        [ 93, 127, 130],
        [ 92, 125, 130],
        [ 91, 125, 130]],

       [[ 78, 126, 130],
        [ 83, 126, 130],
        [ 85, 126, 131],
        ...,
        [ 94, 126, 130],
        [ 94, 125, 130],
        [ 91, 125, 130]],

       ...,

       [[105, 124, 134],
        [110, 124, 133],
        [112, 123, 133],
        ...,
        [119, 124, 130],
        [119, 124, 130],
        [118, 124, 131]],

       [[104, 124, 134],
        [108, 123, 133],
        [111, 123, 133],
        ...,
        [119, 125, 130],
        [118, 124, 130],
        [116, 124, 131]],

       [[102, 124, 132],
        [105, 124, 133],
        [108, 124, 133],
        ...,
        [119, 125, 130],
        [117, 124, 131],
        [116, 124, 130]

In [16]:
model_vgg16_conv = VGG16(
    weights='imagenet',
    include_top=False,
)
model_vgg16_conv.summary()

W0802 23:56:48.293644 140165801953088 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0802 23:56:48.302179 140165801953088 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0802 23:56:48.303809 140165801953088 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0802 23:56:48.319326 140165801953088 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:3976: 

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, None, None, 3)     0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, None, None, 64)    1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, None, None, 64)    36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, None, None, 64)    0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, None, None, 128)   73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, None, None, 128)   147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, None, None, 128)   0         
__________

In [17]:
'''Step 1...
    % Read the image
    original = imread(filename);
    ...
    Step 2...
    % Resize the image to 50x50
    image_resized = imresize(original, scale);
    [M N Z] = size(image_resized);

    % Initialize the output image
    image_out = zeros(height,width);
    image_out = zeros(M,N);
    ...
    Step 3...
    % Convert the image from RGB to YCbCr
    img_ycbcr = rgb2ycbcr(image_resized);
    Cb = img_ycbcr(:,:,2);
    Cr = img_ycbcr(:,:,3);
    ...
    Step 4...
    % Get the central color of the image
    % Expected the hand to be in the central of the image
    central_color = img_ycbcr(int32(M/2),int32(N/2),:);
    Cb_Color = central_color(:,:,2);
    Cr_Color = central_color(:,:,3);
    % Set the range
    Cb_Difference = 15;
    Cr_Difference = 10;
    ...
    Step 5...
    % Detect skin pixels
    [r,c,v] = find(Cb>=Cb_Color-Cr_Difference & Cb<=Cb_Color+Cb_Difference & Cr>=Cr_Color-Cr_Difference & Cr<=Cr_Color+Cr_Difference);
    ...
    Step 6...
    % Mark detected pixels
    for i=1:match_count
        image_out(r(i),c(i)) = 1;
    end
end'''

'Step 1...\n    % Read the image\n    original = imread(filename);\n    ...\n    Step 2...\n    % Resize the image to 50x50\n    image_resized = imresize(original, scale);\n    [M N Z] = size(image_resized);\n\n    % Initialize the output image\n    image_out = zeros(height,width);\n    image_out = zeros(M,N);\n    ...\n    Step 3...\n    % Convert the image from RGB to YCbCr\n    img_ycbcr = rgb2ycbcr(image_resized);\n    Cb = img_ycbcr(:,:,2);\n    Cr = img_ycbcr(:,:,3);\n    ...\n    Step 4...\n    % Get the central color of the image\n    % Expected the hand to be in the central of the image\n    central_color = img_ycbcr(int32(M/2),int32(N/2),:);\n    Cb_Color = central_color(:,:,2);\n    Cr_Color = central_color(:,:,3);\n    % Set the range\n    Cb_Difference = 15;\n    Cr_Difference = 10;\n    ...\n    Step 5...\n    % Detect skin pixels\n    [r,c,v] = find(Cb>=Cb_Color-Cr_Difference & Cb<=Cb_Color+Cb_Difference & Cr>=Cr_Color-Cr_Difference & Cr<=Cr_Color+Cr_Difference);\n    ..

In [ ]:
cv2.namedWindow("imagen", cv2.WINDOW_NORMAL)
cv2.imshow("imagen", img)
cv2.resizeWindow("imagen", 1200, 600);
cv2.waitKey(0)
cv2.destroyAllWindows()

In [ ]:
plt.figure(figsize=(16, 16))
plt.imshow(cv2.cvtColor(img, cv2.COLOR_BGR2RGB), interpolation='bicubic')
plt.xticks([])
plt.yticks([])
plt.axvline(img.shape[1] / 2, c='r', linewidth=4)
plt.show()

In [12]:
from keras.preprocessing.image import ImageDataGenerator
datagen = ImageDataGenerator()

In [31]:
from keras import models, layers, optimizers
from keras.models import Model

imageSize = 100
model1 = VGG16(weights='imagenet', include_top=False, input_shape=(imageSize, imageSize, 3))
optimizer1 = optimizers.Adam()

base_model = model1  # Topless
# Add top layer
x = base_model.output
x = Flatten()(x)
x = Dense(128, activation='relu', name='fc1')(x)
x = Dense(128, activation='relu', name='fc2')(x)
x = Dense(128, activation='relu', name='fc3')(x)
x = Dropout(0.5)(x)
x = Dense(64, activation='relu', name='fc4')(x)

predictions = Dense(6, activation='softmax')(x)
model = Model(inputs=base_model.input, outputs=predictions)


In [32]:
model.compile(optimizer=optimizers.Adam(), loss='categorical_crossentropy', metrics=['accuracy'])

In [14]:
tr_files, te_files, tr_labels, te_labels

from keras.preprocessing.image import ImageDataGenerator
datagen = ImageDataGenerator()
datagen.fit(X_train)

NameError: name 'X_train' is not defined

In [33]:
model.fit(np.array(tr_files), to_categorical(tr_labels), epochs=100, batch_size=64, verbose=1,\
          validation_data=(np.array(va_files), to_categorical(va_labels)))

Train on 1405 samples, validate on 302 samples
Epoch 1/100
1405/1405 [==============================] - 73s 52ms/step - loss: 2.6142 - acc: 0.2093 - val_loss: 1.7505 - val_acc: 0.2517
Epoch 2/100
1405/1405 [==============================] - 82s 58ms/step - loss: 1.7194 - acc: 0.2349 - val_loss: 1.6371 - val_acc: 0.2384
Epoch 3/100
1405/1405 [==============================] - 76s 54ms/step - loss: 1.6757 - acc: 0.2263 - val_loss: 1.6485 - val_acc: 0.2517
Epoch 4/100
1405/1405 [==============================] - 79s 56ms/step - loss: 1.6624 - acc: 0.2299 - val_loss: 1.6385 - val_acc: 0.2583
Epoch 5/100
1405/1405 [==============================] - 104s 74ms/step - loss: 1.6548 - acc: 0.2292 - val_loss: 1.6596 - val_acc: 0.2318
Epoch 6/100
1405/1405 [==============================] - 102s 73ms/step - loss: 1.6416 - acc: 0.2399 - val_loss: 1.6129 - val_acc: 0.2517
Epoch 7/100
1405/1405 [==============================] - 99s 71ms/step - loss: 1.6272 - acc: 0.2356 - val_loss: 1.6081 - val_acc:

KeyboardInterrupt: 

In [ ]:
print(te_labels)

In [37]:
[loss, acc] = model.evaluate(np.array(te_files), to_categorical(te_labels),verbose=1)
print("Accuracy:" + str(acc))

301/301 [==============================] - 0s 1ms/step
Accuracy:1.0


In [38]:
predictions = model.predict_classes((np.array(te_files)))

In [18]:
gesture_names = {0: 'palm',
                 1: 'thumb',
                 2: 'victory',
                 3: 'index',
                 4: 'rock',
                 5: 'oke'}

In [39]:
print(te_labels)

['1', '5', '3', '4', '0', '5', '1', '3', '3', '1', '1', '5', '1', '4', '0', '2', '4', '3', '1', '1', '5', '1', '3', '1', '0', '0', '0', '3', '0', '5', '5', '1', '5', '4', '3', '0', '0', '3', '4', '3', '1', '0', '3', '0', '3', '1', '0', '0', '3', '1', '0', '1', '1', '2', '5', '3', '1', '5', '3', '0', '3', '4', '4', '2', '3', '1', '1', '5', '1', '0', '3', '0', '2', '0', '5', '1', '4', '1', '5', '4', '5', '0', '0', '2', '3', '1', '3', '4', '1', '5', '2', '5', '1', '0', '1', '5', '4', '5', '5', '0', '1', '1', '5', '4', '0', '3', '5', '2', '5', '3', '1', '4', '1', '1', '1', '1', '1', '5', '0', '1', '3', '4', '5', '1', '3', '5', '2', '1', '0', '1', '1', '0', '4', '5', '1', '0', '2', '4', '4', '0', '1', '2', '3', '5', '1', '4', '3', '0', '0', '1', '0', '0', '4', '1', '1', '3', '3', '1', '0', '0', '4', '4', '1', '1', '0', '0', '5', '1', '1', '1', '1', '4', '0', '0', '1', '0', '0', '1', '0', '3', '5', '0', '4', '0', '1', '5', '1', '0', '0', '0', '2', '4', '1', '1', '5', '0', '0', '5', '2', '2',

In [50]:
correct = 0
incorrect = 0
for i in range(len(predictions)):
    if int(te_labels[i]) == int(predictions[i]):
        correct +=1
    else:
        print (f"{te_labels[i]} es distinto a {predictions[i]}")
        incorrect +=1
print(f"Correctas: {correct}, Incorrectas: {incorrect}")

Correctas: 301, Incorrectas: 0


In [ ]:
print(predictions)

In [ ]:
model.save('models/first_model.h5')

In [2]:
from keras.models import load_model
model = load_model('models/first_model.h5')

W0803 12:25:58.017017 140467842656064 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0803 12:25:58.032285 140467842656064 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0803 12:25:58.042958 140467842656064 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:3976: The name tf.nn.max_pool is deprecated. Please use tf.nn.max_pool2d instead.

W0803 12:25:58.068126 140467842656064 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:131: The name tf.get_def

In [ ]:
'''THRESHOLD = 0.8

class_names = {0: 'Palma',
              1: 'Thumb', 2: 'Victoria', 3: 'Índice', 4: 'Rock&Roll', 5: 'OK'}

cap = cv2.VideoCapture(0)

while True:
    
    ret, frame = cap.read()
    
    model.setInput(cv2.dnn.blobFromImage(frame, size=(300, 300), swapRB=True))
    
    output = model.forward()[0,0,:,:]
    
    for detection in output:
        confidence = detection[2]
        if confidence > THRESHOLD:
            class_id = detection[1]
            class_name = class_names[class_id]
            # print(confidence, class_name)
            
            # rectangles!
            
            box_x=detection[3]
            box_y=detection[4]
            box_width=detection[5]
            box_height=detection[6]
            
            height, width, ch = frame.shape
            
            box_x = detection[3] * width
            box_y = detection[4] * height
            box_width = detection[5] * width
            box_height = detection[6] * height
                                          
            cv2.rectangle(frame, 
                          (int(box_x),
                           int(box_y)),
                          (int(box_width),
                           int(box_height)),
                          (0, 0, 255), 
                          thickness=2)
            
            cv2.putText(frame, 
                        class_name + ' ' + str(round(confidence, 2)),
                        (int(box_x), 
                         int(box_y+.05*height)),
                        cv2.FONT_HERSHEY_SIMPLEX,
                        1,
                        (0, 0, 255))
    
    cv2.imshow('object_detection', frame)
    
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()'''

In [2]:
from keras.models import load_model
model = load_model('models/first_model.h5')

W0803 13:06:02.020033 140582241670976 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0803 13:06:02.047756 140582241670976 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0803 13:06:02.062592 140582241670976 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:3976: The name tf.nn.max_pool is deprecated. Please use tf.nn.max_pool2d instead.

W0803 13:06:02.093064 140582241670976 deprecation_wrapper.py:119] From /home/alfonso/miniconda3/envs/final_project/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:131: The name tf.get_def

In [13]:
def processImage(img):
    img_resized = cv2.resize(img, (100,100), interpolation = cv2.INTER_AREA)
    imgYCC = cv2.cvtColor(img_resized, cv2.COLOR_BGR2YCR_CB)
    height, width = imgYCC.shape[:2]
    middle_color = imgYCC[25,25]
    y_range = 20
    cb_range = 15
    cr_range = 10
    return imgYCC

img_prueba = cv2.imread('inputs/prueba/rock.jpg', cv2.IMREAD_COLOR)

'''cv2.imshow('Original Image',img_prueba)
cv2.waitKey(0) # waits until a key is pressed
cv2.destroyAllWindows()'''

img_processed = processImage(img_prueba)



prediction = int(model.predict_classes((np.array(img_processed))))


print(prediction)

ValueError: Error when checking input: expected conv2d_7_input to have 4 dimensions, but got array with shape (100, 100, 3)

In [ ]:
def processImage(img):
    img_resized = cv2.resize(img, (100,100), interpolation = cv2.INTER_AREA)
    imgYCC = cv2.cvtColor(img_resized, cv2.COLOR_BGR2YCR_CB)
    height, width = imgYCC.shape[:2]
    middle_color = imgYCC[25,25]
    y_range = 20
    cb_range = 15
    cr_range = 10
    return imgYCC

from keras.models import load_model
model = load_model('models/first_model.h5')

threshold = 0.8

class_names = {0: 'Palma',
              1: 'Thumb', 2: 'Victoria', 3: 'Índice', 4: 'Rock&Roll', 5: 'OK'}

cap = cv2.VideoCapture(0)

while True:

    ret, frame = cap.read()
    
    
    
    width = frame.shape[0] // 2
    height = frame.shape[0] // 2
    '''    img_processed = processImage(frame)
    
    prediction = int(model.predict_classes((np.array(img_processed))))
    
    print(prediction)'''
    
    direccion = 0
    
    while True:
        if direccion == 0:
            width += 1
            height += 1
            cv2.circle(frame, (width, height), 10, (255, 255, 255), 16)
    
            cv2.imshow('object_detection', frame)
    
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
            
    if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    
cap.release()
cv2.destroyAllWindows()